# Word2Vec

## Introducción

Word2Vec es una técnica que se utiliza para obtener representaciones vectoriales de palabras. Estas representaciones son útiles para realizar tareas de procesamiento de lenguaje natural, como la clasificación de texto, la traducción automática, la generación de texto, etc. Su objetivo es capturar las relaciones semánticas y sintácticas entre palabras basándose en su contexto dentro de un corpus de texto. Fue introducido por Mikolov et al. en 2013.

Esta técnica se basa en la hipótesis distribucional, que establece que las palabras que aparecen en contextos similares tienen significados similares. Por lo tanto, Word2Vec se entrena para predecir las palabras vecinas de una palabra dada, utilizando un corpus de texto como datos de entrenamiento.

Tiene dos variantes principales: Skip-gram y Continuous Bag of Words (CBOW). La diferencia entre ambas radica en la forma en que se plantea el problema de predicción. En el caso de Skip-gram, se predice el contexto a partir de una palabra dada, mientras que en CBOW se predice la palabra a partir de su contexto.

Por ejemplo en el texto "El gato come pescado", si utilizamos una ventana de tamaño 2, el contexto de la palabra "come" sería "El gato pescado". En el caso de Skip-gram, se trataría de predecir "El", "gato", "pescado" a partir de "come":

| Entrada | Salida |
|---------|--------|
| come    | El     |
| come    | gato   |
| come    | pescado|

Mientras que en el caso de CBOW, se trataría de predecir "come" a partir de "El", "gato", "pescado":

| Entrada | Salida |
|---------|--------|
| El      | come   |
| gato    | come   |
| pescado | come   |

En este notebook, vamos a utilizar la implementación de Word2Vec de la librería Gensim para entrenar un modelo de Skip-gram y explorar las representaciones vectoriales de palabras obtenidas.

La **representación inicial de palabras** en Word2Vec es una representación **discreta y esparsa** conocida como **one-hot encoding**. Es el punto de partida antes de que las palabras sean transformadas en vectores densos y continuos mediante el aprendizaje en Word2Vec. Vamos a desglosarlo con ejemplos para clarificar cómo funciona.

---

### 1. **One-Hot Encoding: Representación Básica**
Dado un vocabulario de $ V $ palabras, asignamos un índice único a cada palabra. Luego, representamos cada palabra como un vector de dimensión $ V $, donde todas las posiciones son 0 excepto una, que es 1.

#### Ejemplo Simple
Supongamos un vocabulario con las siguientes palabras:
$$
\text{Vocabulario} = \{\text{gato, perro, ratón, queso}\}
$$

Asignamos índices:
- $ \text{gato} \to 0 $
- $ \text{perro} \to 1 $
- $ \text{ratón} \to 2 $
- $ \text{queso} \to 3 $

La representación **one-hot** para cada palabra será:
$$
\text{gato} = [1, 0, 0, 0], \quad \text{perro} = [0, 1, 0, 0], \quad \text{ratón} = [0, 0, 1, 0], \quad \text{queso} = [0, 0, 0, 1]
$$

---

### 2. **Propiedades del One-Hot Encoding**
1. **Alta Dimensionalidad**:
   Si el vocabulario tiene $ V = 10,000 $ palabras, cada palabra estará representada por un vector de tamaño $ 10,000 $, con un único valor de 1.

2. **Discretas y Esparzas**:
   Solo un elemento del vector es 1, mientras que el resto son ceros. Esto significa que la representación es **esparsa** y ocupa mucho espacio de memoria.

3. **Sin Captura de Relación Semántica**:
   La representación one-hot no tiene en cuenta ninguna relación entre palabras. Por ejemplo:
   - $ \text{gato} = [1, 0, 0, 0] $
   - $ \text{perro} = [0, 1, 0, 0] $

   Aunque $ \text{gato} $ y $ \text{perro} $ están semánticamente relacionados (ambos son animales), sus representaciones one-hot son **ortogonales** y no comparten ninguna similitud matemática.

---

### 3. **Limitaciones del One-Hot Encoding**
#### A. **Dimensión del Vector**
A medida que el vocabulario crece, la dimensión $ V $ se vuelve enorme, lo que hace que esta representación sea ineficiente.

#### B. **Falta de Información Semántica**
La distancia entre vectores no refleja similitudes entre palabras. Por ejemplo:
$$
\text{Distancia Euclidiana}(\text{gato}, \text{perro}) = \text{Distancia Euclidiana}(\text{gato}, \text{queso}) = \sqrt{2}
$$
Esto significa que $ \text{gato} $ está tan "cerca" de $ \text{perro} $ como de $ \text{queso} $, lo cual no es intuitivo.

#### C. **Escalabilidad en Modelos**
Los modelos de aprendizaje automático necesitan procesar estos vectores de alta dimensionalidad, lo cual aumenta la complejidad computacional y limita el rendimiento.

---

### 4. **Transición a Representaciones Densas**
La motivación de Word2Vec es superar estas limitaciones al transformar las palabras en **vectores densos** y de menor dimensión ($ d $) que capturen relaciones semánticas. Por ejemplo:

- Representación inicial (one-hot): $ \text{gato} = [1, 0, 0, 0] $
- Representación Word2Vec: $ \text{gato} = [0.2, -0.4] \text{, perro}  =[0.1, -0.3] $

---

### 5. **Ejemplo de Representación Inicial en un Contexto Real**
Imaginemos una oración: 
$$
\text{"El gato persigue al ratón"}
$$

1. Vocabulario:
   $$
   \{\text{el, gato, persigue, al, ratón}\}
   $$

2. Índices de las palabras:
   - $ \text{el} \to 0 $
   - $ \text{gato} \to 1 $
   - $ \text{persigue} \to 2 $
   - $ \text{al} \to 3 $
   - $ \text{ratón} \to 4 $

3. Representaciones one-hot:
   - $ \text{el} = [1, 0, 0, 0, 0] $
   - $ \text{gato} = [0, 1, 0, 0, 0] $
   - $ \text{persigue} = [0, 0, 1, 0, 0] $
   - $ \text{al} = [0, 0, 0, 1, 0] $
   - $ \text{ratón} = [0, 0, 0, 0, 1] $

Cuando esta oración pasa por un modelo como Word2Vec, estas representaciones iniciales se transforman en vectores densos que reflejan las relaciones semánticas entre palabras. Por ejemplo:

$$
\text{gato} \approx [0.3, -0.2, 0.8], \quad \text{ratón} \approx [0.2, -0.1, 0.7]
$$

Estas nuevas representaciones permiten cálculos más avanzados, como medir la similitud semántica entre palabras.

In [1]:
### Librerias necesarias Word2Vec

import gensim
from gensim.models import Word2Vec

import numpy as np
import pandas as pd
import re
import os

## 2. Cargar el texto

Para este ejercicio inicial usaremos un texto sencillo, el cual se cargará en una variable.

In [2]:
texto_1 = """Hace varios años, en el pelotón de fusilamiento, el coronel Aureliano Buendía había de recordar aquella tarde remota en que su padre lo llevó a conocer el hielo. """
texto_2 = """Hace tanto tiempo que no me acuerdo de nada, pero recuerdo que mi padre me llevó a conocer el hielo. """
texto_3 = """Hace tiempo que ocurrió la era de hielo, ahorita que solo soy un  perezoso recuerdo aquellos días tan bellos con mis amigos, un mamut y un dientes de sable. """

corpus = [texto_1, texto_2, texto_3]

## 3. Preprocesamiento

El preprocesamiento es una etapa importante en el procesamiento de lenguaje natural. En esta etapa se eliminan las palabras que no aportan información, como los signos de puntuación, las palabras vacías, etc.

In [4]:
############# Preprocesamiento de texto ####################
def preprocesamiento(texto):
    texto = texto.lower()
    texto = re.sub(r"[\W\d_]+", " ", texto)
    texto = texto.split()

    return texto

corpus_procesado = [preprocesamiento(texto) for texto in corpus]

print(corpus_procesado)

[['hace', 'varios', 'años', 'en', 'el', 'pelotón', 'de', 'fusilamiento', 'el', 'coronel', 'aureliano', 'buendía', 'había', 'de', 'recordar', 'aquella', 'tarde', 'remota', 'en', 'que', 'su', 'padre', 'lo', 'llevó', 'a', 'conocer', 'el', 'hielo'], ['hace', 'tanto', 'tiempo', 'que', 'no', 'me', 'acuerdo', 'de', 'nada', 'pero', 'recuerdo', 'que', 'mi', 'padre', 'me', 'llevó', 'a', 'conocer', 'el', 'hielo'], ['hace', 'tiempo', 'que', 'ocurrió', 'la', 'era', 'de', 'hielo', 'ahorita', 'que', 'solo', 'soy', 'un', 'perezoso', 'recuerdo', 'aquellos', 'días', 'tan', 'bellos', 'con', 'mis', 'amigos', 'un', 'mamut', 'y', 'un', 'dientes', 'de', 'sable']]


# **4. Arquitectura de Word2Vec**

## **CBOW (Continuous Bag of Words)**

CBOW busca predecir una palabra objetivo $ w_t $ a partir de sus palabras de contexto. Este proceso transforma representaciones **esparsas** (vectores one-hot) en representaciones **densas** (embeddings) que capturan relaciones semánticas globales entre palabras.

---

### **Notación Preliminar**
1. **Vocabulario**: $ V $, el tamaño total del vocabulario.
2. **Dimensión del embedding**: $ d $, la dimensión del espacio donde proyectamos las palabras.
3. **Matrices de embedding**:
   - $ \mathbf{W} \in \mathbb{R}^{V \times d} $: Matriz de embeddings de entrada.
   - $ \mathbf{U} \in \mathbb{R}^{V \times d} $: Matriz de embeddings de salida.
4. **Vector one-hot**:
   - Cada palabra $ w $ se representa como $ \mathbf{x} \in \mathbb{R}^V $, donde $ x_i = 1 $ si $ i $ es el índice de $ w $, y $ x_j = 0 $ para $ j \neq i $.

---

## **CBOW en Lenguaje Matricial**

### **Forward Pass**

#### **Paso 1: Entrada - Palabras de Contexto**

Dada la frase:
$$
\text{"El gato persigue al ratón"}
$$

Queremos predecir $ w_t = \text{"persigue"} $, utilizando como contexto:
$$
\{\text{"El"}, \text{"gato"}, \text{"al"}, \text{"ratón"}\}.
$$

1. Asignamos índices al vocabulario:
$$
\{\text{"El"} \to 0, \text{"gato"} \to 1, \text{"persigue"} \to 2, \text{"al"} \to 3, \text{"ratón"} \to 4\}.
$$

2. Representamos las palabras de contexto como vectores one-hot:
$$
\mathbf{X} =
\begin{bmatrix}
1 & 0 & 0 & 0 & 0 \\  % "El"
0 & 1 & 0 & 0 & 0 \\  % "gato"
0 & 0 & 0 & 1 & 0 \\  % "al"
0 & 0 & 0 & 0 & 1     % "ratón"
\end{bmatrix}
\in \mathbb{R}^{4 \times 5}.
$$

---

#### **Paso 2: Transformación - Embeddings densos**

La matriz de embeddings $ \mathbf{W} \in \mathbb{R}^{V \times d} $ transforma las representaciones esparsas en vectores densos. La operación es:
$$
\mathbf{E}_{\text{contexto}} = \mathbf{X} \mathbf{W}.
$$

Supongamos que $ d = 2 $ y:
$$
\mathbf{W} =
\begin{bmatrix}
0.1 & 0.2 \\  % "El"
0.3 & 0.4 \\  % "gato"
0.5 & 0.6 \\  % "persigue"
0.7 & 0.8 \\  % "al"
0.9 & 1.0     % "ratón"
\end{bmatrix}.
$$

Entonces:
$$
\mathbf{E}_{\text{contexto}} =
\begin{bmatrix}
0.1 & 0.2 \\  % "El"
0.3 & 0.4 \\  % "gato"
0.7 & 0.8 \\  % "al"
0.9 & 1.0     % "ratón"
\end{bmatrix}
\in \mathbb{R}^{4 \times 2}.
$$

Cada fila representa un embedding denso que captura las características semánticas latentes de cada palabra.

---

#### **Paso 3: Promedio de los embeddings**

Para resumir el contexto, calculamos el promedio de los vectores densos:
$$
\mathbf{v}_{\text{contexto}} = \frac{1}{2k} \sum_{i=1}^{2k} \mathbf{E}_{\text{contexto}}[i, :].
$$

En este caso:
$$
\mathbf{v}_{\text{contexto}} = \frac{1}{4} \begin{bmatrix} 0.1+0.3+0.7+0.9 & 0.2+0.4+0.8+1.0 \end{bmatrix} = \begin{bmatrix} 0.5 & 0.6 \end{bmatrix}.
$$

---

#### **Paso 4: Proyección al espacio del vocabulario**

Proyectamos $ \mathbf{v}_{\text{contexto}} $ al espacio del vocabulario utilizando la matriz de salida $ \mathbf{U} \in \mathbb{R}^{V \times d} $:
$$
\mathbf{z} = \mathbf{U} \mathbf{v}_{\text{contexto}}.
$$

Por ejemplo, si:
$$
\mathbf{U} =
\begin{bmatrix}
0.2 & 0.3 \\  % "El"
0.4 & 0.5 \\  % "gato"
0.6 & 0.7 \\  % "persigue"
0.8 & 0.9 \\  % "al"
1.0 & 1.1     % "ratón"
\end{bmatrix},
$$

entonces:
$$
\mathbf{z} =
\begin{bmatrix}
0.2 & 0.3 \\ 
0.4 & 0.5 \\ 
0.6 & 0.7 \\ 
0.8 & 0.9 \\ 
1.0 & 1.1
\end{bmatrix}
\cdot
\begin{bmatrix}
0.5 \\ 
0.6
\end{bmatrix}
=
\begin{bmatrix}
0.28 \\  % "El"
0.49 \\  % "gato"
0.70 \\  % "persigue"
0.91 \\  % "al"
1.12     % "ratón"
\end{bmatrix}.
$$

---

#### **Paso 5: Softmax**

Finalmente, aplicamos softmax para convertir $ \mathbf{z} $ en una distribución de probabilidad:
$$
P(w_t | \text{contexto}) = \frac{\exp(z_i)}{\sum_{j=1}^V \exp(z_j)}.
$$

La palabra con la mayor probabilidad será la predicción $ \hat{w}_t $, que debería ser "persigue".

---

### **3. Por qué CBOW Encuentra Relaciones Densas**

1. **De esparso a denso**:
   Transformar $ \mathbf{x} $ mediante $ \mathbf{W} $ reduce la dimensionalidad (de $ V $ a $ d $) y captura relaciones semánticas latentes.

2. **Relaciones semánticas globales**:
   Los embeddings densos reflejan la coocurrencia de palabras en contextos similares. Palabras como "gato" y "ratón", que aparecen juntas, tendrán vectores cercanos.

3. **Eficiencia computacional**:
   Al calcular un promedio, se reduce el impacto de palabras menos informativas como artículos y preposiciones.

---

### **4. Impacto en Semántica y Sintaxis**

1. **Semántica**:
   - CBOW captura relaciones globales. Por ejemplo, "gato" y "perro" tendrán embeddings cercanos si aparecen en contextos similares.

2. **Sintaxis**:
   - CBOW ignora el orden de las palabras. Por ejemplo, "El gato persigue al ratón" y "El ratón persigue al gato" tendrán la misma representación promedio, lo que puede ser una limitación en tareas sensibles al orden.


## **Skip-gram**

En Skip-gram, la dirección del problema se invierte: en lugar de predecir la palabra objetivo $ w_t $ a partir del contexto, ahora utilizamos $ w_t $ para predecir cada palabra del contexto. Esto significa que cada palabra central está asociada a múltiples predicciones, una para cada palabra en su ventana de contexto.

---

### **1. ¿Qué se optimiza en Skip-gram?**

El objetivo del modelo Skip-gram es **maximizar la probabilidad condicional de las palabras del contexto** $ \{w_{t-k}, \ldots, w_{t-1}, w_{t+1}, \ldots, w_{t+k}\} $, dado la palabra central $ w_t $. 

La pérdida del modelo está definida como la log-verosimilitud negativa sobre todas las palabras del contexto:
$$
\mathcal{L} = -\sum_{t=1}^T \sum_{j=-k, j \neq 0}^k \log P(w_{t+j} | w_t),
$$
donde:
- $ P(w_{t+j} | w_t) $ es la probabilidad predicha de que $ w_{t+j} $ sea una palabra del contexto, dado $ w_t $.
- $ T $ es el número total de palabras en el corpus.
- $ k $ es el tamaño de la ventana de contexto.

---

### **2. Probabilidad condicional en Skip-gram**

La probabilidad condicional $ P(w_{t+j} | w_t) $ se calcula utilizando la función softmax, de manera similar a CBOW:
$$
P(w_{t+j} | w_t) = \frac{\exp(\mathbf{u}_{w_{t+j}}^\top \mathbf{v}_{w_t})}{\sum_{i=1}^V \exp(\mathbf{u}_i^\top \mathbf{v}_{w_t})},
$$
donde:
- $ \mathbf{v}_{w_t} $ es el embedding de la palabra central $ w_t $, obtenido de la matriz $ \mathbf{W} $.
- $ \mathbf{u}_{w_{t+j}} $ es el embedding de salida de la palabra del contexto $ w_{t+j} $, tomado de la matriz $ \mathbf{U} $.
- $ V $ es el tamaño del vocabulario.

La optimización ajusta los parámetros de $ \mathbf{W} $ y $ \mathbf{U} $ para maximizar la probabilidad de las palabras reales del contexto dadas las palabras centrales.

---

### **3. ¿Cómo se originan las probabilidades en Skip-gram?**

Desglosemos este proceso con un ejemplo.

---

#### Ejemplo: **"El gato persigue al ratón"**

Queremos predecir el contexto $ \{\text{"El"}, \text{"gato"}, \text{"al"}, \text{"ratón"}\} $ dado $ w_t = \text{"persigue"} $.

---

### Paso 1: Representación One-Hot de la Palabra Central

Asignamos índices al vocabulario:
$$
\{\text{"El"} \to 0, \text{"gato"} \to 1, \text{"persigue"} \to 2, \text{"al"} \to 3, \text{"ratón"} \to 4\}.
$$

La palabra central $ w_t = \text{"persigue"} $ se representa como un vector one-hot:
$$
\mathbf{x}_{w_t} =
\begin{bmatrix}
0 \\  % "El"
0 \\  % "gato"
1 \\  % "persigue"
0 \\  % "al"
0     % "ratón"
\end{bmatrix}
\in \mathbb{R}^{5}.
$$

---

### Paso 2: Transformación a Embedding Denso

Multiplicamos $ \mathbf{x}_{w_t} $ por la matriz de embeddings de entrada $ \mathbf{W} \in \mathbb{R}^{V \times d} $ para obtener el embedding denso de la palabra central:
$$
\mathbf{v}_{w_t} = \mathbf{x}_{w_t}^\top \mathbf{W}.
$$

Supongamos que $ d = 2 $ y:
$$
\mathbf{W} =
\begin{bmatrix}
0.1 & 0.2 \\  % "El"
0.3 & 0.4 \\  % "gato"
0.5 & 0.6 \\  % "persigue"
0.7 & 0.8 \\  % "al"
0.9 & 1.0     % "ratón"
\end{bmatrix}.
$$

La multiplicación selecciona la fila correspondiente a $ w_t = \text{"persigue"} $:
$$
\mathbf{v}_{w_t} =
\begin{bmatrix}
0.5 & 0.6
\end{bmatrix}.
$$

---

### Paso 3: Proyección al Espacio del Vocabulario

Para cada palabra del contexto $ w_{t+j} $, calculamos las puntuaciones $ z_{w_{t+j}} $ mediante la proyección:
$$
z_i = \mathbf{u}_i^\top \mathbf{v}_{w_t},
$$
donde $ \mathbf{u}_i $ es el vector de salida de la palabra $ i $, tomado de la matriz $ \mathbf{U} \in \mathbb{R}^{V \times d} $.

Supongamos:
$$
\mathbf{U} =
\begin{bmatrix}
0.2 & 0.3 \\  % "El"
0.4 & 0.5 \\  % "gato"
0.6 & 0.7 \\  % "persigue"
0.8 & 0.9 \\  % "al"
1.0 & 1.1     % "ratón"
\end{bmatrix}.
$$

Calculamos las puntuaciones para todas las palabras:
$$
\mathbf{z} = \mathbf{U} \mathbf{v}_{w_t}.
$$

Realizando la multiplicación:
$$
\mathbf{z} =
\begin{bmatrix}
0.2 & 0.3 \\ 
0.4 & 0.5 \\ 
0.6 & 0.7 \\ 
0.8 & 0.9 \\ 
1.0 & 1.1
\end{bmatrix}
\cdot
\begin{bmatrix}
0.5 \\ 
0.6
\end{bmatrix}.
$$

1. Para "El":
   $$
   z_{\text{"El"}} = 0.2 \cdot 0.5 + 0.3 \cdot 0.6 = 0.1 + 0.18 = 0.28.
   $$
2. Para "gato":
   $$
   z_{\text{"gato"}} = 0.4 \cdot 0.5 + 0.5 \cdot 0.6 = 0.2 + 0.3 = 0.49.
   $$
3. Repetimos para todas las palabras:
   $$
   \mathbf{z} =
   \begin{bmatrix}
   0.28 \\  % "El"
   0.49 \\  % "gato"
   0.70 \\  % "persigue"
   0.91 \\  % "al"
   1.12     % "ratón"
   \end{bmatrix}.
   $$

---

### Paso 4: Conversión a Probabilidades (Softmax)

La función softmax normaliza estas puntuaciones:
$$
P(w_{t+j} | w_t) = \frac{\exp(z_{w_{t+j}})}{\sum_{i=1}^V \exp(z_i)}.
$$

1. Calculamos $ \exp(z_i) $:
   $$
   \exp(\mathbf{z}) =
   \begin{bmatrix}
   1.32 \\ 
   1.63 \\ 
   2.01 \\ 
   2.48 \\ 
   3.07
   \end{bmatrix}.
   $$

2. Calculamos la suma:
   $$
   \sum_{i=1}^V \exp(z_i) = 1.32 + 1.63 + 2.01 + 2.48 + 3.07 = 10.51.
   $$

3. Dividimos cada $ \exp(z_i) $ entre la suma para obtener probabilidades:
   $$
   P(w_{t+j} = \text{"El"} | w_t) = \frac{1.32}{10.51} \approx 0.126,
   $$
   $$
   P(w_{t+j} = \text{"gato"} | w_t) = \frac{1.63}{10.51} \approx 0.155,
   $$
   y así sucesivamente.

---

### **4. Relación entre Probabilidades y Optimización**

- Cada palabra del contexto tiene su propia probabilidad condicional $ P(w_{t+j} | w_t) $.
- El modelo ajusta los parámetros

## 4. Entrenamiento del modelo

Una vez que se ha preprocesado el texto, se puede entrenar el modelo Word2Vec. Para ello, se utiliza la clase `Word2Vec` de la librería Gensim. Se pueden configurar varios parámetros, como el tamaño del vector, la ventana de contexto, el número de iteraciones, etc.

In [7]:
[token for elemento in corpus_procesado for token in elemento ]

['hace',
 'varios',
 'años',
 'en',
 'el',
 'pelotón',
 'de',
 'fusilamiento',
 'el',
 'coronel',
 'aureliano',
 'buendía',
 'había',
 'de',
 'recordar',
 'aquella',
 'tarde',
 'remota',
 'en',
 'que',
 'su',
 'padre',
 'lo',
 'llevó',
 'a',
 'conocer',
 'el',
 'hielo',
 'hace',
 'tanto',
 'tiempo',
 'que',
 'no',
 'me',
 'acuerdo',
 'de',
 'nada',
 'pero',
 'recuerdo',
 'que',
 'mi',
 'padre',
 'me',
 'llevó',
 'a',
 'conocer',
 'el',
 'hielo',
 'hace',
 'tiempo',
 'que',
 'ocurrió',
 'la',
 'era',
 'de',
 'hielo',
 'ahorita',
 'que',
 'solo',
 'soy',
 'un',
 'perezoso',
 'recuerdo',
 'aquellos',
 'días',
 'tan',
 'bellos',
 'con',
 'mis',
 'amigos',
 'un',
 'mamut',
 'y',
 'un',
 'dientes',
 'de',
 'sable']

In [8]:
vocabulario=set([token for elemento in corpus_procesado for token in elemento ])
vocabulario

{'a',
 'acuerdo',
 'ahorita',
 'amigos',
 'aquella',
 'aquellos',
 'aureliano',
 'años',
 'bellos',
 'buendía',
 'con',
 'conocer',
 'coronel',
 'de',
 'dientes',
 'días',
 'el',
 'en',
 'era',
 'fusilamiento',
 'había',
 'hace',
 'hielo',
 'la',
 'llevó',
 'lo',
 'mamut',
 'me',
 'mi',
 'mis',
 'nada',
 'no',
 'ocurrió',
 'padre',
 'pelotón',
 'perezoso',
 'pero',
 'que',
 'recordar',
 'recuerdo',
 'remota',
 'sable',
 'solo',
 'soy',
 'su',
 'tan',
 'tanto',
 'tarde',
 'tiempo',
 'un',
 'varios',
 'y'}

In [9]:
len(vocabulario)

52

In [11]:
' '.join(corpus_procesado[0])

'hace varios años en el pelotón de fusilamiento el coronel aureliano buendía había de recordar aquella tarde remota en que su padre lo llevó a conocer el hielo'

In [12]:
############# Entrenamiento de modelo Word2Vec ####################

modelo = Word2Vec(corpus_procesado, vector_size=5, window=5, min_count=1, sg=0)

### Aqui cada parametro significa lo siguiente:
# vector_size: Dimension de los vectores de palabras
# window: Numero de palabras que se toman en cuenta para predecir la siguiente palabra
# min_count: Frecuencia minima de palabras para ser considerada
# sg: 0 para CBOW y 1 para Skip-gram



In [13]:
print(modelo.wv.key_to_index)

{'de': 0, 'que': 1, 'el': 2, 'hace': 3, 'hielo': 4, 'un': 5, 'recuerdo': 6, 'en': 7, 'padre': 8, 'llevó': 9, 'a': 10, 'conocer': 11, 'me': 12, 'tiempo': 13, 'solo': 14, 'aureliano': 15, 'mis': 16, 'remota': 17, 'tarde': 18, 'aquella': 19, 'recordar': 20, 'había': 21, 'buendía': 22, 'coronel': 23, 'ahorita': 24, 'fusilamiento': 25, 'amigos': 26, 'pelotón': 27, 'mamut': 28, 'y': 29, 'años': 30, 'varios': 31, 'su': 32, 'con': 33, 'lo': 34, 'bellos': 35, 'era': 36, 'la': 37, 'ocurrió': 38, 'mi': 39, 'soy': 40, 'pero': 41, 'nada': 42, 'acuerdo': 43, 'perezoso': 44, 'no': 45, 'dientes': 46, 'tanto': 47, 'aquellos': 48, 'días': 49, 'tan': 50, 'sable': 51}


In [14]:
print(modelo.wv["hielo"])


[0.14623532 0.10140524 0.13515386 0.01525731 0.12701781]


## 5. Exploración de las representaciones vectoriales

Una vez entrenado el modelo, se pueden explorar las representaciones vectoriales de las palabras. Por ejemplo, se pueden obtener las palabras más similares a una palabra dada, o realizar operaciones de álgebra de vectores para encontrar relaciones entre palabras.

In [15]:
#### Explorar representaciones vectoriales de palabras ####

print(modelo.wv.most_similar("hielo"))

[('varios', 0.9723590612411499), ('coronel', 0.7841842174530029), ('pelotón', 0.7699286341667175), ('tarde', 0.731586217880249), ('tiempo', 0.6933352947235107), ('y', 0.6796896457672119), ('fusilamiento', 0.5221249461174011), ('solo', 0.5042399764060974), ('pero', 0.49508294463157654), ('con', 0.45632946491241455)]


In [16]:
print(modelo.wv.most_similar("coronel"))

[('varios', 0.8150733113288879), ('hielo', 0.7841840386390686), ('tiempo', 0.6788021922111511), ('solo', 0.6308004856109619), ('y', 0.5896435379981995), ('no', 0.48532769083976746), ('acuerdo', 0.48292607069015503), ('mi', 0.44453248381614685), ('pero', 0.432786762714386), ('que', 0.42994925379753113)]


In [7]:
### ALgebra de palabras ###

print(modelo.wv.most_similar(positive=["hielo", "padre"], negative=["perezoso"]))



[('amigos', 0.23566339910030365), ('ocurrió', 0.2183714061975479), ('el', 0.19603098928928375), ('mi', 0.16588948667049408), ('tan', 0.14655449986457825), ('no', 0.13405673205852509), ('que', 0.13025563955307007), ('tiempo', 0.12840767204761505), ('un', 0.08849232643842697), ('conocer', 0.0849686861038208)]


### Implementación de word2vec en Python

Usaremos un dataset de ejemmlo para entrenar un modelo Word2Vec.

In [22]:
import pandas as pd

DF_corpus = pd.read_csv("ejemplo.csv")

DF_corpus.head()

Unnamed: 0                                    Cosas Negativas
0          12                                         Ventilador
1          19  Realicé una reserva por bookin y me cobraron v...
2          23     no pusierton toallas y no tienen agua caliente
3          25  Me cobraron un valor mayor, al que figuraba en...
4          32                                                  .

In [24]:
corpus=DF_corpus['Cosas Negativas'].dropna().values

corpus_procesado = [preprocesamiento(texto) for texto in corpus]

In [25]:
len(set([token for elemento in corpus_procesado for token in elemento ]))

60846

In [39]:
modelo = Word2Vec(corpus_procesado, vector_size=100, window=5, min_count=1, sg=0, epochs=100, seed=42)


In [40]:
print(modelo.wv.key_to_index)

{'la': 0, 'de': 1, 'no': 2, 'el': 3, 'y': 4, 'que': 5, 'a': 6, 'en': 7, 'the': 8, 'las': 9, 'me': 10, 'se': 11, 'un': 12, 'habitación': 13, 'muy': 14, 'es': 15, 'hotel': 16, 'para': 17, 'del': 18, 'una': 19, 'por': 20, 'con': 21, 'and': 22, 'to': 23, 'al': 24, 'los': 25, 'was': 26, 'lo': 27, 'in': 28, 'i': 29, 'nos': 30, 'desayuno': 31, 'room': 32, 'ruido': 33, 'not': 34, 'era': 35, 'baño': 36, 'it': 37, 'agua': 38, 'había': 39, 'estaba': 40, 'habitaciones': 41, 'of': 42, 'pero': 43, 'o': 44, 'personal': 45, 'is': 46, 'fue': 47, 'todo': 48, 'for': 49, 'le': 50, 'servicio': 51, 'mi': 52, 'hay': 53, 'si': 54, 'ni': 55, 'noche': 56, 'mucho': 57, 'sin': 58, 't': 59, 'cama': 60, 'we': 61, 'they': 62, 'como': 63, 'más': 64, 'cuando': 65, 'mal': 66, 'tenía': 67, 'recepción': 68, 'e': 69, 'solo': 70, 'at': 71, 'poco': 72, 'very': 73, 'ya': 74, 'on': 75, 'that': 76, 'son': 77, 'nada': 78, 'atención': 79, 'there': 80, 'had': 81, 'tiene': 82, 'porque': 83, 'reserva': 84, 'check': 85, 'you': 86, '

In [41]:
print(modelo.wv["malo"])

[-2.2068834   4.2576375  -1.7633535  -1.4869928   4.182575   -0.6225192
 -0.5320494  -1.7132622   2.678149    0.59029514 -0.5681679   1.496683
  0.14790338  1.5315617  -0.18066289  0.89577955 -2.523334   -4.1695786
 -2.6549113  -2.1142178   1.2639868   3.061897   -0.03972566  2.236487
 -1.134351    1.5665442   1.1938052   1.5493736  -0.06555377  2.1022758
 -3.549513    1.5537817  -2.004112   -1.2311668   0.653955   -0.1723231
  1.4245406  -1.1871647   0.784299    2.0234344   1.0258852  -0.0633399
  1.6830142   1.1126902   3.2349765   0.48449406 -0.19496906  3.1821086
 -1.3582999  -4.645926    0.9881065   2.1539962  -1.5539349   1.6852305
 -1.1863776   3.2013373  -1.8614179  -1.8085451   2.6097152   0.64429986
 -0.98144484  4.4568453  -1.6809127   0.17737022  1.0802383   0.96006167
 -6.001505   -2.337507   -2.5911758   0.08171848 -1.7790109   1.2059462
 -0.56984735  4.050474    1.449553   -0.6413174   0.96583027 -0.09398981
  3.8545098  -0.26276377 -0.08393486 -2.9420104  -1.5316579  -1

In [42]:
print(modelo.wv.most_similar("malo"))

[('regular', 0.7173362374305725), ('deficiente', 0.7150459885597229), ('pésimo', 0.7096670269966125), ('básico', 0.6889232397079468), ('bueno', 0.6699802875518799), ('lento', 0.6671026945114136), ('pobre', 0.6391055583953857), ('mal', 0.6159226298332214), ('pequeño', 0.6003609299659729), ('feo', 0.5978437066078186)]


In [43]:
print(modelo.wv.most_similar("sábanas"))

[('sabanas', 0.8531106114387512), ('toallas', 0.742468535900116), ('cobijas', 0.7074674367904663), ('fundas', 0.6978349685668945), ('almohadas', 0.6621938347816467), ('manchas', 0.6409747004508972), ('paredes', 0.6206626892089844), ('cortinas', 0.5894428491592407), ('sbanas', 0.5839039087295532), ('camas', 0.5825182199478149)]


In [44]:
print(modelo.wv.most_similar("toallas"))

[('cobijas', 0.7785037755966187), ('sábanas', 0.742468535900116), ('sabanas', 0.7311030030250549), ('toalla', 0.6889472603797913), ('almohadas', 0.6482136249542236), ('tohallas', 0.6308388710021973), ('paños', 0.6149953007698059), ('llaves', 0.5872368216514587), ('cosas', 0.5859378576278687), ('paredes', 0.5798693895339966)]


In [45]:
modelo.wv.vectors.shape

(60846, 100)

In [46]:
### VIsualización de palabras | T-sne | plotly###

from sklearn.manifold import TSNE
import plotly.express as px

proyecciones_tsne=TSNE(n_components=2).fit_transform(modelo.wv.vectors)
print(proyecciones_tsne.shape)

(60846, 2)


In [47]:
px.scatter(x=proyecciones_tsne[:,0], y=proyecciones_tsne[:,1],hover_data=[list(modelo.wv.key_to_index.keys())])

In [8]:
import tensorflow as tf
import numpy as np
import re

# Preprocesamiento del texto
def preprocesamiento(texto):
    texto = texto.lower()
    texto = re.sub(r"[\W\d_]+", " ", texto)
    texto = texto.split()
    return texto

corpus_procesado = [preprocesamiento(texto) for texto in corpus]

2024-11-23 13:57:09.071530: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-11-23 13:57:10.629767: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [10]:
corpus_procesado

[['hace',
  'varios',
  'años',
  'en',
  'el',
  'pelotón',
  'de',
  'fusilamiento',
  'el',
  'coronel',
  'aureliano',
  'buendía',
  'había',
  'de',
  'recordar',
  'aquella',
  'tarde',
  'remota',
  'en',
  'que',
  'su',
  'padre',
  'lo',
  'llevó',
  'a',
  'conocer',
  'el',
  'hielo'],
 ['hace',
  'tanto',
  'tiempo',
  'que',
  'no',
  'me',
  'acuerdo',
  'de',
  'nada',
  'pero',
  'recuerdo',
  'que',
  'mi',
  'padre',
  'me',
  'llevó',
  'a',
  'conocer',
  'el',
  'hielo'],
 ['hace',
  'tiempo',
  'que',
  'ocurrió',
  'la',
  'era',
  'de',
  'hielo',
  'ahorita',
  'que',
  'solo',
  'soy',
  'un',
  'perezoso',
  'recuerdo',
  'aquellos',
  'días',
  'tan',
  'bellos',
  'con',
  'mis',
  'amigos',
  'un',
  'mamut',
  'y',
  'un',
  'dientes',
  'de',
  'sable']]

In [11]:
# Crear un diccionario de palabras y sus índices
vocab = set(word for sentence in corpus_procesado for word in sentence)
word2idx = {word: idx for idx, word in enumerate(vocab)}
idx2word = {idx: word for word, idx in word2idx.items()}
vocab_size = len(vocab)

print(word2idx)

{'buendía': 0, 'que': 1, 'me': 2, 'la': 3, 'recordar': 4, 'hielo': 5, 'llevó': 6, 'dientes': 7, 'coronel': 8, 'ocurrió': 9, 'pero': 10, 'no': 11, 'tan': 12, 'remota': 13, 'varios': 14, 'padre': 15, 'acuerdo': 16, 'a': 17, 'hace': 18, 'su': 19, 'ahorita': 20, 'mamut': 21, 'un': 22, 'de': 23, 'había': 24, 'perezoso': 25, 'y': 26, 'aquellos': 27, 'lo': 28, 'bellos': 29, 'aquella': 30, 'era': 31, 'nada': 32, 'mi': 33, 'tarde': 34, 'amigos': 35, 'mis': 36, 'en': 37, 'pelotón': 38, 'conocer': 39, 'tanto': 40, 'sable': 41, 'días': 42, 'soy': 43, 'el': 44, 'tiempo': 45, 'aureliano': 46, 'años': 47, 'con': 48, 'recuerdo': 49, 'fusilamiento': 50, 'solo': 51}


In [13]:
# Crear datos de entrenamiento para Word2Vec
def generate_context_word_pairs(corpus, window_size):
    context_length = window_size * 2
    for words in corpus:
        sentence_length = len(words)
        for index, word in enumerate(words):
            context_words = []
            start = index - window_size
            end = index + window_size + 1

            context_words.append([word2idx[words[i]] 
                                  for i in range(start, end) 
                                  if 0 <= i < sentence_length 
                                  and i != index])
            target_word = word2idx[word]

            yield (context_words[0], target_word)

window_size = 2
data = list(generate_context_word_pairs(corpus_procesado, window_size))

In [14]:
data

[([14, 47], 18),
 ([18, 47, 37], 14),
 ([18, 14, 37, 44], 47),
 ([14, 47, 44, 38], 37),
 ([47, 37, 38, 23], 44),
 ([37, 44, 23, 50], 38),
 ([44, 38, 50, 44], 23),
 ([38, 23, 44, 8], 50),
 ([23, 50, 8, 46], 44),
 ([50, 44, 46, 0], 8),
 ([44, 8, 0, 24], 46),
 ([8, 46, 24, 23], 0),
 ([46, 0, 23, 4], 24),
 ([0, 24, 4, 30], 23),
 ([24, 23, 30, 34], 4),
 ([23, 4, 34, 13], 30),
 ([4, 30, 13, 37], 34),
 ([30, 34, 37, 1], 13),
 ([34, 13, 1, 19], 37),
 ([13, 37, 19, 15], 1),
 ([37, 1, 15, 28], 19),
 ([1, 19, 28, 6], 15),
 ([19, 15, 6, 17], 28),
 ([15, 28, 17, 39], 6),
 ([28, 6, 39, 44], 17),
 ([6, 17, 44, 5], 39),
 ([17, 39, 5], 44),
 ([39, 44], 5),
 ([40, 45], 18),
 ([18, 45, 1], 40),
 ([18, 40, 1, 11], 45),
 ([40, 45, 11, 2], 1),
 ([45, 1, 2, 16], 11),
 ([1, 11, 16, 23], 2),
 ([11, 2, 23, 32], 16),
 ([2, 16, 32, 10], 23),
 ([16, 23, 10, 49], 32),
 ([23, 32, 49, 1], 10),
 ([32, 10, 1, 33], 49),
 ([10, 49, 33, 15], 1),
 ([49, 1, 15, 2], 33),
 ([1, 33, 2, 6], 15),
 ([33, 15, 6, 17], 2),
 ([15, 2,

In [16]:
# Separar datos en X (contexto) e y (palabra objetivo)
X, y = zip(*data)
# Hagamos padding para que todos los contextos tengan la misma longitud
X = tf.keras.preprocessing.sequence.pad_sequences(X)
# Convertir a arrays de numpy
X = np.array(X)
y = np.array(y)

In [17]:
X

array([[ 0,  0, 14, 47],
       [ 0, 18, 47, 37],
       [18, 14, 37, 44],
       [14, 47, 44, 38],
       [47, 37, 38, 23],
       [37, 44, 23, 50],
       [44, 38, 50, 44],
       [38, 23, 44,  8],
       [23, 50,  8, 46],
       [50, 44, 46,  0],
       [44,  8,  0, 24],
       [ 8, 46, 24, 23],
       [46,  0, 23,  4],
       [ 0, 24,  4, 30],
       [24, 23, 30, 34],
       [23,  4, 34, 13],
       [ 4, 30, 13, 37],
       [30, 34, 37,  1],
       [34, 13,  1, 19],
       [13, 37, 19, 15],
       [37,  1, 15, 28],
       [ 1, 19, 28,  6],
       [19, 15,  6, 17],
       [15, 28, 17, 39],
       [28,  6, 39, 44],
       [ 6, 17, 44,  5],
       [ 0, 17, 39,  5],
       [ 0,  0, 39, 44],
       [ 0,  0, 40, 45],
       [ 0, 18, 45,  1],
       [18, 40,  1, 11],
       [40, 45, 11,  2],
       [45,  1,  2, 16],
       [ 1, 11, 16, 23],
       [11,  2, 23, 32],
       [ 2, 16, 32, 10],
       [16, 23, 10, 49],
       [23, 32, 49,  1],
       [32, 10,  1, 33],
       [10, 49, 33, 15],


In [18]:
# Definir el modelo Word2Vec
embedding_dim = 100

# Input layer
inputs = tf.keras.Input(shape=(window_size * 2,), dtype=tf.int32)

# Embedding layer
embedding = tf.keras.layers.Embedding(input_dim=vocab_size, output_dim=embedding_dim, input_length=window_size * 2)(inputs)

# Mean of embeddings
mean_embedding = tf.reduce_mean(embedding, axis=1)

# Output layer
outputs = tf.keras.layers.Dense(vocab_size, activation='softmax')(mean_embedding)

# Compile the model
model = tf.keras.Model(inputs=inputs, outputs=outputs)
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy')

# Entrenar el modelo
model.fit(X, y, epochs=100, verbose=1)

# Obtener las representaciones vectoriales de las palabras
word_vectors = model.get_layer('embedding').get_weights()[0]
print(word_vectors)

/home/isaac-zainea/miniconda3/envs/nlp_ean/lib/python3.10/site-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(
2024-11-23 16:19:02.087971: E external/local_xla/xla/stream_executor/cuda/cuda_driver.cc:282] failed call to cuInit: CUDA_ERROR_UNKNOWN: unknown error
2024-11-23 16:19:02.088092: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:134] retrieving CUDA diagnostic information for host: isaaczainea-TUF-Gaming
2024-11-23 16:19:02.088102: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:141] hostname: isaaczainea-TUF-Gaming
2024-11-23 16:19:02.088316: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:165] libcuda reported version is: 535.216.3
2024-11-23 16:19:02.088342: I external/local_xla/xla/stream_executor/cuda/cuda_diagnostics.cc:169] kernel reported version is: 535.216.1
2024-11-23 16:19:02.088350: E external/local_xla/xla/stream_executor/cuda/c

ValueError: A KerasTensor cannot be used as input to a TensorFlow function. A KerasTensor is a symbolic placeholder for a shape and dtype, used when constructing Keras Functional models or Keras Functions. You can only use it as input to a Keras layer or a Keras operation (from the namespaces `keras.layers` and `keras.operations`). You are likely doing something like:

```
x = Input(...)
...
tf_fn(x)  # Invalid.
```

What you should do instead is wrap `tf_fn` in a layer:

```
class MyLayer(Layer):
    def call(self, x):
        return tf_fn(x)

x = MyLayer()(x)
```


## 6. Conclusiones

En este notebook, hemos visto cómo entrenar un modelo Word2Vec utilizando la librería Gensim y explorar las representaciones vectoriales de palabras obtenidas. Estas representaciones son útiles para realizar tareas de procesamiento de lenguaje natural, como la clasificación de texto, la traducción automática, la generación de texto, etc.